# Data Access

In [0]:
spark.conf.set("fs.azure.account.auth.type..dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type..dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set("fs.azure.account.oauth2.client.id..dfs.core.windows.net", "")
spark.conf.set("fs.azure.account.oauth2.client.secret..dfs.core.windows.net", "")
spark.conf.set("fs.azure.account.oauth2.client.endpoint..dfs.core.windows.net", "https://login.microsoftonline.com//oauth2/token")
# Azure OAuth configuration - Credentials stored securely in Databricks secrets
# Actual client_id, client_secret and tenant_id removed for security
     

# Datebase Creation

In [0]:
%sql
CREATE DATABASE golddatabase

# Data Reading and Writing and Creating Delta Tables

In [0]:
dbutils.fs.ls('abfss://silver@nyctaxidataproject1.dfs.core.windows.net')

[FileInfo(path='abfss://silver@nyctaxidataproject1.dfs.core.windows.net/trip_type/', name='trip_type/', size=0, modificationTime=1764841031000),
 FileInfo(path='abfss://silver@nyctaxidataproject1.dfs.core.windows.net/trip_zone/', name='trip_zone/', size=0, modificationTime=1764841033000),
 FileInfo(path='abfss://silver@nyctaxidataproject1.dfs.core.windows.net/trips2024data/', name='trips2024data/', size=0, modificationTime=1764841880000)]

# Data Reading

**Importing Libraries**

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

## Reading Parquet Data

**Data Zone**

**Variables**

In [0]:
silver = "abfss://silver@nyctaxidataproject1.dfs.core.windows.net"
gold = "abfss://gold@nyctaxidataproject1.dfs.core.windows.net"

In [0]:
df_zone = spark.read.format('parquet')\
               .option('inferSchema',True)\
               .option('header',True)\
               .load(f'{silver}/trip_zone')

In [0]:
df_zone.display()

LocationID Borough Zone service_zone zone1 zone2 1 EWR Newark Airport EWR Newark Airport null 2 Queens Jamaica Bay Boro Zone Jamaica Bay null 3 Bronx Allerton/Pelham Gardens Boro Zone Allerton Pelham Gardens 4 Manhattan Alphabet City Yellow Zone Alphabet City null 5 Staten Island Arden Heights Boro Zone Arden Heights null 6 Staten Island Arrochar/Fort Wadsworth Boro Zone Arrochar Fort Wadsworth 7 Queens Astoria Boro Zone Astoria null 8 Queens Astoria Park Boro Zone Astoria Park null 9 Queens Auburndale Boro Zone Auburndale null 10 Queens Baisley Park Boro Zone Baisley Park null 11 Brooklyn Bath Beach Boro Zone Bath Beach null 12 Manhattan Battery Park Yellow Zone Battery Park null 13 Manhattan Battery Park City Yellow Zone Battery Park City null 14 Brooklyn Bay Ridge Boro Zone Bay Ridge null 15 Queens Bay Terrace/Fort Totten Boro Zone Bay Terrace Fort Totten 16 Queens Bayside Boro Zone Bayside null 17 Brooklyn Bedford Boro Zone Bedford null 18 Bronx Bedford Park Boro Zone Bedford Park null 19 Queens Bellerose Boro Zone Bellerose null 20 Bronx Belmont Boro Zone Belmont null 21 Brooklyn Bensonhurst East Boro Zone Bensonhurst East null 22 Brooklyn Bensonhurst West Boro Zone Bensonhurst West null 23 Staten Island Bloomfield/Emerson Hill Boro Zone Bloomfield Emerson Hill 24 Manhattan Bloomingdale Yellow Zone Bloomingdale null 25 Brooklyn Boerum Hill Boro Zone Boerum Hill null 26 Brooklyn Borough Park Boro Zone Borough Park null 27 Queens Breezy Point/Fort Tilden/Riis Beach Boro Zone Breezy Point Fort Tilden 28 Queens Briarwood/Jamaica Hills Boro Zone Briarwood Jamaica Hills 29 Brooklyn Brighton Beach Boro Zone Brighton Beach null 30 Queens Broad Channel Boro Zone Broad Channel null 31 Bronx Bronx Park Boro Zone Bronx Park null 32 Bronx Bronxdale Boro Zone Bronxdale null 33 Brooklyn Brooklyn Heights Boro Zone Brooklyn Heights null 34 Brooklyn Brooklyn Navy Yard Boro Zone Brooklyn Navy Yard null 35 Brooklyn Brownsville Boro Zone Brownsville null 36 Brooklyn Bushwick North Boro Zone Bushwick North null 37 Brooklyn Bushwick South Boro Zone Bushwick South null 38 Queens Cambria Heights Boro Zone Cambria Heights null 39 Brooklyn Canarsie Boro Zone Canarsie null 40 Brooklyn Carroll Gardens Boro Zone Carroll Gardens null 41 Manhattan Central Harlem Boro Zone Central Harlem null 42 Manhattan Central Harlem North Boro Zone Central Harlem North null 43 Manhattan Central Park Yellow Zone Central Park null 44 Staten Island Charleston/Tottenville Boro Zone Charleston Tottenville 45 Manhattan Chinatown Yellow Zone Chinatown null 46 Bronx City Island Boro Zone City Island null 47 Bronx Claremont/Bathgate Boro Zone Claremont Bathgate 48 Manhattan Clinton East Yellow Zone Clinton East null 49 Brooklyn Clinton Hill Boro Zone Clinton Hill null 50 Manhattan Clinton West Yellow Zone Clinton West null 51 Bronx Co-Op City Boro Zone Co-Op City null 52 Brooklyn Cobble Hill Boro Zone Cobble Hill null 53 Queens College Point Boro Zone College Point null 54 Brooklyn Columbia Street Boro Zone Columbia Street null 55 Brooklyn Coney Island Boro Zone Coney Island null 56 Queens Corona Boro Zone Corona null 57 Queens Corona Boro Zone Corona null 58 Bronx Country Club Boro Zone Country Club null 59 Bronx Crotona Park Boro Zone Crotona Park null 60 Bronx Crotona Park East Boro Zone Crotona Park East null 61 Brooklyn Crown Heights North Boro Zone Crown Heights North null 62 Brooklyn Crown Heights South Boro Zone Crown Heights South null 63 Brooklyn Cypress Hills Boro Zone Cypress Hills null 64 Queens Douglaston Boro Zone Douglaston null 65 Brooklyn Downtown Brooklyn/MetroTech Boro Zone Downtown Brooklyn MetroTech 66 Brooklyn DUMBO/Vinegar Hill Boro Zone DUMBO Vinegar Hill 67 Brooklyn Dyker Heights Boro Zone Dyker Heights null 68 Manhattan East Chelsea Yellow Zone East Chelsea null 69 Bronx East Concourse/Concourse Village Boro Zone East Concourse Concourse Village 70 Queens East Elmhurst Boro Zone East Elmhurst null 71 Brooklyn East Flatbush/Farragut Boro Zone East Fl

**Trip Type**

In [0]:
df_type = spark.read.format('parquet')\
               .option('inferSchema',True)\
               .option('header',True)\
               .load(f'{silver}/trip_type')

In [0]:
df_type.display()

trip_type trip_description 1 Street-hail 2 Dispatch

In [0]:
df_type.write.format("delta")\
    .mode("overwrite")\
    .save(f"{gold}/trip_type")


**Trips Data**

In [0]:
df_trips = spark.read.format('parquet')\
               .option('inferSchema',True)\
               .option('header',True)\
               .load(f'{silver}/trips2024data')

In [0]:
df_trips.display()

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee trip_pickup_date trip_pickup_year trip_pickup_month trip_dropoff_date trip_dropoff_year trip_dropoff_month 2 2024-10-01T00:30:44 2024-10-01T00:48:26 1 3.0 1 N 162 246 1 18.4 1.0 0.5 1.5 0.0 1.0 24.9 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:12:20 2024-10-01T00:25:25 1 2.2 1 N 48 236 1 14.2 3.5 0.5 3.8 0.0 1.0 23.0 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:04:46 2024-10-01T00:13:52 1 2.7 1 N 142 24 1 13.5 3.5 0.5 3.7 0.0 1.0 22.2 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:12:10 2024-10-01T00:23:01 1 3.1 1 N 233 75 1 14.2 3.5 0.5 2.0 0.0 1.0 21.2 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:30:22 2024-10-01T00:30:39 1 0.0 1 N 262 262 3 3.0 3.5 0.5 0.0 0.0 1.0 8.0 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:31:20 2024-10-01T00:36:00 2 0.97 1 N 137 137 1 7.2 1.0 0.5 2.44 0.0 1.0 14.64 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:42:57 2024-10-01T00:49:01 1 1.3 1 N 142 48 1 7.9 3.5 0.5 2.55 0.0 1.0 15.45 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:59:55 2024-10-01T01:02:24 1 0.5 1 N 230 161 1 5.1 3.5 0.5 2.0 0.0 1.0 12.1 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:00:47 2024-10-01T00:04:22 0 1.1 1 N 142 237 1 7.2 3.5 0.5 3.0 0.0 1.0 15.2 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:17:36 2024-10-01T00:26:22 1 2.2 1 N 162 145 1 11.4 3.5 0.5 3.3 0.0 1.0 19.7 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:49:00 2024-10-01T00:52:20 1 0.6 1 N 229 162 1 5.1 3.5 0.5 2.0 0.0 1.0 12.1 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:07:26 2024-10-01T00:13:20 1 0.9 1 N 162 162 1 7.9 1.0 0.5 3.87 0.0 1.0 16.77 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:17:11 2024-10-01T00:25:00 1 1.33 1 N 162 230 1 9.3 1.0 0.5 2.0 0.0 1.0 16.3 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:00:34 2024-10-01T00:05:13 1 1.79 1 N 211 234 1 9.3 1.0 0.5 2.86 0.0 1.0 17.16 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-09-30T23:58:40 2024-10-01T00:20:26 1 5.16 1 N 142 7 1 24.7 1.0 0.5 0.0 0.0 1.0 29.7 2.5 0.0 2024-09-30 2024 9 2024-10-01 2024 10 1 2024-10-01T00:55:29 2024-10-01T01:42:35 1 11.3 99 N 161 197 1 39.5 0.0 0.5 0.0 6.94 1.0 47.94 0.0 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:08:59 2024-10-01T00:40:58 1 20.6 1 N 132 243 2 76.5 2.75 0.5 0.0 6.94 1.0 87.69 0.0 1.75 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:18:38 2024-10-01T00:36:47 2 7.42 1 N 239 247 4 -33.1 -1.0 -0.5 0.0 0.0 -1.0 -38.1 -2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:18:38 2024-10-01T00:36:47 2 7.42 1 N 239 247 4 33.1 1.0 0.5 0.0 0.0 1.0 38.1 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:39:33 2024-10-01T00:53:59 1 4.49 1 N 247 60 2 21.9 1.0 0.5 0.0 0.0 1.0 24.4 0.0 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:24:14 2024-10-01T00:35:48 1 1.89 1 N 234 231 1 12.8 1.0 0.5 2.5 0.0 1.0 20.3 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T01:00:05 2024-10-01T01:11:18 1 4.1 1 N 233 74 1 17.7 1.0 0.5 4.54 0.0 1.0 27.24 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T00:32:23 2024-10-01T00:42:38 1 1.3 1 N 262 236 1 10.0 3.5 0.5 1.0 0.0 1.0 16.0 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:29:02 2024-10-01T00:39:09 1 1.8 1 N 263 238 1 12.8 1.0 0.5 4.45 0.0 1.0 22.25 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:40:10 2024-10-01T00:46:36 1 1.07 1 N 238 24 1 8.6 1.0 0.5 2.72 0.0 1.0 16.32 2.5 0.0 2024-10-01 2024 10 2024-10-01 2024 10 2 2024-10-01T00:28:52 2024-10-01T00:51:34 2 9.94 1 N 138 107 1 40.8 6.0 0.5 10.16 0.0 1.0 62.71 2.5 1.75 2024-10-01 2024 10 2024-10-01 2024 10 1 2024-10-01T0

In [0]:
df_trips.write.format("delta")\
    .mode("overwrite")\
    .save(f"{gold}/trips2024data")
